<a href="https://colab.research.google.com/github/okechukwuchude/Automating-Medical-Coding/blob/main/Colab.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:
import os
import json
import stanza
import csv
import pandas as pd

# Build an English pipeline
stanza.download('en', package='mimic', processors={'ner': 'i2b2'}) # download English model
nlp = stanza.Pipeline('en', package='mimic', processors={'ner': 'i2b2'}) # initialize English neural pipeline

C:\Users\okechukwu chude\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\tqdm\auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2024-03-21 18:18:14 INFO: Downloaded file to C:\Users\okechukwu chude\stanza_resources\resources.json
2024-03-21 18:18:14 INFO: Downloading these customized packages for language: en (English)...
| Processor       | Package        |
------------------------------------
| tokenize        | mimic          |
| pos             | mimic_charlm   |
| lemma           | mimic_nocharlm |
| depparse        | mimic_charlm   |
| ner             | i2b2           |
| forward_charlm  | mimic          |
| pretrain        | mimic          |
| backward_charlm | mimic          |

2024-03-21 18:18:14 INFO: File exists: C:\Users\okechukwu chude\stanza_resource

In [3]:
# Function to process text using Stanza
def process_text_with_stanza(text):
    doc = nlp(text)
    return doc

In [4]:
# Global variable to store all extracted texts
extracted_texts = []

In [5]:
def extract_info_from_json(json_file_path, hadm_id_set):
    global extracted_texts

    # Open the JSON file
    with open(json_file_path, 'r') as file:
        # Load JSON data from the file
        data = json.load(file)

        # Extract 'hadm_id' and 'comment' from the JSON data
        hadm_id = data.get('hadm_id', None)
        comment = data.get('comment', None)

        # If 'hadm_id' is not found, print a warning message
        if hadm_id is None:
            print(f"Warning: 'hadm_id' not found in {json_file_path}")
            return None

        # Add 'hadm_id' to the set
        hadm_id_set.add(hadm_id)

        # Extract 'notes' from the JSON data
        notes = data.get('notes', [])

        # Iterate through each note
        for note in notes:
            note_info = {}  # Initialize a dictionary to store note information

            # Add 'hadm_id' to the note information
            note_info['hadm_id'] = hadm_id

            # Extract information from the note
            note_info['note_id'] = note.get('note_id', None)
            note_info['category'] = note.get('category', None)
            note_info['description'] = note.get('description', None)

            # Extract annotations from the note
            annotations = note.get('annotations', [])
            annotations_info = []  # Initialize a list to store annotation information

            # Iterate through each annotation in the note
            for annotation in annotations:
                annotation_info = {}  # Initialize a dictionary to store annotation information

                # Extract information from the annotation
                annotation_info['begin'] = annotation.get('begin', None)
                annotation_info['end'] = annotation.get('end', None)
                annotation_info['code'] = annotation.get('code', None)
                annotation_info['code_system'] = annotation.get('code_system', None)
                annotation_info['description'] = annotation.get('description', None)
                annotation_info['type'] = annotation.get('type', None)
                annotation_info['covered_text'] = annotation.get('covered_text', None)

                annotations_info.append(annotation_info)  # Append annotation information to the list

            note_info['annotations'] = annotations_info  # Add annotations information to the note
            note_info['text'] = note.get('text', None)

            # Process text with Stanza
            if note_info['text']:
                processed_text = process_text_with_stanza(note_info['text'])
                note_info['processed_text'] = processed_text

                # Extract sentence information and generate labels
                sentence_info = []
                for sent in processed_text.sentences:
                    tokens = [word.text for word in sent.words]
                    labels = ['O'] * len(tokens)  # Initialize labels as 'O'

                    for annotation in note_info['annotations']:
                        begin = annotation['begin']
                        end = annotation['end']

                        word_indices = find_word_indices(sent.words, begin, end)

                        # Assign labels
                        if word_indices:
                            start_idx, end_idx = word_indices[0], word_indices[-1]
                            labels[start_idx] = 'B'
                            for idx in range(start_idx + 1, end_idx + 1):
                                labels[idx] = 'I'
                        # for idx in word_indices:
                        #     if sent.words[idx].start_char == begin:
                        #         labels[idx] = 'B'
                        #     elif sent.words[idx].start_char > begin and sent.words[idx].end_char < end:
                        #         labels[idx] = 'I'

                    sentence_info.append({
                        'sentence_id': sent.index,
                        'words': tokens,
                        'labels': labels
                    })

                    # Print the result for each sentence
                    print('Sentence:', ' '.join(tokens))
                    print('Labels:', ' '.join(labels))
                    print()

                note_info['sentence_info'] = sentence_info

            extracted_texts.append(note_info)  # Append note information to the global variable

#

In [6]:
def find_word_indices(words, begin, end):
    # Create an empty list to store the indices of words found within the given range
    word_indices = []

    # Iterate through each token in the list of tokens
    for idx, word in enumerate(words):
        # Check if the start character of the token matches the beginning of the range
        # or if the token spans the beginning of the range
        if word.start_char == begin or (word.start_char < begin and word.end_char > begin):
            # If it matches, add the index of the token to the list of word indices
            word_indices.append(idx)
        # Check if the end character of the token matches the end of the range
        # or if the token spans the end of the range
        if word.end_char == end or (word.start_char < end and word.end_char > end):
            # If it matches, add the index of the token to the list of word indices
            word_indices.append(idx)
            break

    # Return the list of word indices found within the given range
    return word_indices

In [7]:
def generate_labels(words, annotations, start_token_idx, end_token_idx):
    labels = ['O'] * len(words)

    for annotation in annotations:
        code = annotation['code']

        # # Update labels for the matched words
        # if start_token_idx is not None and end_token_idx is not None:
        #     labels[start_token_idx] = f'B-{code}'
        #     for idx in range(start_token_idx + 1, end_token_idx + 1):
        #         labels[idx] = f'I-{code}'

    return labels

In [8]:
# Function to search for JSON files in a given folder and its subfolders

def search_files(folder_path):
    # Set to store unique hadm_id values
    hadm_id_set = set()

    # Recursively search for JSON files in the folder and its subfolders
    for root, dirs, files in os.walk(folder_path):
        for filename in files:
            if filename.endswith('.json'):
                # Construct the full path to the JSON file
                json_file_path = os.path.join(root, filename)
                print("Processing:", json_file_path)
                # Call extract_info_from_json function to extract information from the JSON file
                extract_info_from_json(json_file_path, hadm_id_set)
                # Print a separator after processing each file
                print("=" * 50)

    # Print the count of unique hadm_id values
    print("Total unique hadm_id count:", len(hadm_id_set))



In [9]:
# Specify the path to the main folder containing subfolders with JSON files
main_folder_path = r'C:\Users\okechukwu chude\Documents\NLP\text extraction\Automating-Medical-Coding\testing'

# Call the search_files function to start searching for JSON files in the main folder and its subfolders
search_files(main_folder_path)

Processing: C:\Users\okechukwu chude\Documents\NLP\text extraction\Automating-Medical-Coding\testing\gold\Inpatient\ICD-10\1.0\100197-ICD-10.json


Sentence: Admission Date : [ **2136-10-23 **] Discharge Date : [ **2136-10-24 **]
Labels: O O O O O O O O O O O O

Sentence: Date of Birth : [ ** 2056-7-14 **] Sex : M
Labels: O O O O O O O O O O O

Sentence: Service : NEUROSURGERY
Labels: O O O

Sentence: Allergies : No Known Allergies / Adverse Drug Reactions
Labels: O O O O O O O O O

Sentence: Attending :[** First Name3 ( LF ) 1835 **] Chief Complaint : Found down
Labels: O O O O O O O O O O O O O O

Sentence: Major Surgical or Invasive Procedure : None
Labels: O O O O O O O

Sentence: History of Present Illness : 80M p/w a large R IPH with intraventricular extension , midline shift , and hydrocephalus .
Labels: O O O O O O O O O O B O B I O O O O O B O

Sentence: The patient was found lying face up in his bathtub after having shaved .
Labels: O O O O O O O O O O O O O O

Sentence: There was no water in the tub and the shower was not turned on .
Labels: O O O O O O O O O O O O O O O

Sentence: He was found by a neighbor .
Labels: O

In [10]:
import pandas as pd

# Function to create a DataFrame from the extracted sentence information
def create_dataframe(extracted_texts):
    data = []

    for note_info in extracted_texts:
        if 'sentence_info' in note_info:
            for sentence_info in note_info['sentence_info']:
                words = sentence_info['words']
                labels = sentence_info['labels']

                for word, label in zip(words, labels):
                    data.append({
                        'hadm_id': note_info['hadm_id'],
                        'note_id': note_info['note_id'],
                        'sentence_id': sentence_info['sentence_id'],
                        'word': word,
                        'label': label
                    })

    df = pd.DataFrame(data)
    return df

df = create_dataframe(extracted_texts)
print(df)

        hadm_id  note_id  sentence_id          word label
0        100197    25762            0     Admission     O
1        100197    25762            0          Date     O
2        100197    25762            0             :     O
3        100197    25762            0             [     O
4        100197    25762            0  **2136-10-23     O
...         ...      ...          ...           ...   ...
472262   149623   538274           19          time     O
472263   149623   538274           19         spent     O
472264   149623   538274           19             :     O
472265   149623   538274           19            31     O
472266   149623   538274           19       minutes     O

[472267 rows x 5 columns]


In [11]:
label_counts = df['label'].value_counts()
print(label_counts)

label
O    459991
I      6781
B      5495
Name: count, dtype: int64


In [72]:
token_df= df.drop(['hadm_id', 'note_id',], axis=1)

In [73]:
token_df

sentence_id          word label
0                 0     Admission     O
1                 0          Date     O
2                 0             :     O
3                 0             [     O
4                 0  **2136-10-23     O
...             ...           ...   ...
472262           19          time     O
472263           19         spent     O
472264           19             :     O
472265           19            31     O
472266           19       minutes     O

[472267 rows x 3 columns]

In [14]:
token_df.rename(columns = {'word':'words', 'label':'labels'}, inplace = True)

In [15]:
token_df.head()

sentence_id         words labels
0            0     Admission      O
1            0          Date      O
2            0             :      O
3            0             [      O
4            0  **2136-10-23      O

In [16]:
x = token_df[['sentence_id', 'words']]
y = token_df['labels']

SPLITTING DATA

In [17]:
from sklearn.model_selection import train_test_split
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size = 0.3)

In [18]:
#build the training and test data
train_data = pd.DataFrame({'sentence_id': x_train['sentence_id'], 'words': x_train['words'], 'labels': y_train})
test_data = pd.DataFrame({'sentence_id': x_test['sentence_id'], 'words': x_test['words'], 'labels': y_test})

In [19]:
train_data

sentence_id       words labels
217019            7           ,      O
454491           37         jvd      O
439185           24           /      O
470226            3   CONDITION      O
16769             9        test      O
...             ...         ...    ...
450881            8         out      O
117629           17      rounds      O
415902           17      report      O
356771            2   Antitoxin      O
462840           26  identified      O

[330586 rows x 3 columns]

MODEL TRAINING

BERT

In [20]:
pip install simpletransformers

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [21]:
from simpletransformers.ner import NERModel, NERArgs

In [22]:
label = token_df['labels'].unique().tolist()
label

['O', 'B', 'I']

In [25]:
args = NERArgs()
args.num_train_epochs = 10
args.learning_rate = 1e-4
args.overwrite_output_dir = True
args.train_batch_size = 32
args.eval_batch_size = 32

In [26]:
model = NERModel('bert', 'bert-base-cased', labels=label, args=args, use_cuda = False)

Some weights of BertForTokenClassification were not initialized from the model checkpoint at bert-base-cased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [27]:
from sklearn.metrics import accuracy_score

model.train_model(train_data, eval_data = test_data, acc = accuracy_score)

Epoch 10 of 10: 100%|██████████| 10/10 [53:43<00:00, 322.39s/it]


(160, 0.07990432815131499)

In [28]:
result, model_outputs, preds_list = model.eval_model(test_data)

Running Evaluation: 100%|██████████| 16/16 [01:48<00:00,  6.77s/it]


In [29]:
result

{'eval_loss': 0.06948929579630203,
 'precision': 0.28901734104046245,
 'recall': 0.16778523489932887,
 'f1_score': 0.21231422505307854}

In [30]:
prediction, model_output = model.predict(['There is also intraventricular extension into the ipsilateral and contralateral lateral ventricles.'])

Running Prediction: 100%|██████████| 1/1 [00:00<00:00,  3.77it/s]


In [31]:
prediction

[[{'There': 'O'},
  {'is': 'O'},
  {'also': 'O'},
  {'intraventricular': 'O'},
  {'extension': 'O'},
  {'into': 'O'},
  {'the': 'O'},
  {'ipsilateral': 'I'},
  {'and': 'O'},
  {'contralateral': 'O'},
  {'lateral': 'O'},
  {'ventricles.': 'I'}]]

BioBERT

In [32]:
bio_label = token_df['labels'].unique().tolist()
bio_label

['O', 'B', 'I']

In [33]:
# Initialize NER model arguments
args = NERArgs()
args.num_train_epochs = 10  # Number of training epochs
args.learning_rate = 2e-5   # Learning rate
args.overwrite_output_dir = True
args.train_batch_size = 32
args.eval_batch_size = 32

In [35]:
# Create the NER model with BioBERT
model = NERModel('bert', 'dmis-lab/biobert-base-cased-v1.2', args=args, labels=bio_label, use_cuda=False)


Some weights of BertForTokenClassification were not initialized from the model checkpoint at dmis-lab/biobert-base-cased-v1.2 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [36]:
# Train the model
model.train_model(train_data)

# Evaluate the model on test data
bio_result, model_outputs, preds_list = model.eval_model(test_data)

Running Evaluation: 100%|██████████| 16/16 [02:08<00:00,  8.02s/it]


In [37]:
bio_result

{'eval_loss': 0.051469424899551086,
 'precision': 0.33076923076923076,
 'recall': 0.14429530201342283,
 'f1_score': 0.20093457943925233}

In [38]:

predictions, raw_outputs = model.predict(["T[**Name2 (NI) **] was extubated on [**10-24**] without"])
print(predictions)


Running Prediction: 100%|██████████| 1/1 [00:00<00:00,  1.84it/s]

[[{'T[**Name2': 'O'}, {'(NI)': 'O'}, {'**]': 'O'}, {'was': 'O'}, {'extubated': 'O'}, {'on': 'O'}, {'[**10-24**]': 'O'}, {'without': 'O'}]]


Hyperparameter Tuning

In [46]:
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.3, random_state=42)
x_train, x_val, y_train, y_val = train_test_split(x_train, y_train, test_size=0.2, random_state=42)

# Build the training, validation, and test data
train_data = pd.DataFrame({'sentence_id': x_train['sentence_id'], 'words': x_train['words'], 'labels': y_train})
val_data = pd.DataFrame({'sentence_id': x_val['sentence_id'], 'words': x_val['words'], 'labels': y_val})
test_data = pd.DataFrame({'sentence_id': x_test['sentence_id'], 'words': x_test['words'], 'labels': y_test})


In [69]:
from sklearn.metrics import accuracy_score
from simpletransformers.ner import NERModel, NERArgs
import logging


# Define hyperparameters to search over
param_grid = {
    'learning_rate': [1e-5, 2e-5, 3e-5],
    'num_train_epochs': [1, 2, 3],
    'train_batch_size': [16, 32, 64]
}

# Initialize your model
model = NERModel('bert', 'dmis-lab/biobert-base-cased-v1.2', args=args, labels=bio_label, use_cuda=False)

best_accuracy = 0
best_params = {}

# Split test_data into batches to avoid memory issues
test_batches = [test_data[i:i+32] for i in range(0, len(test_data), 32)]

# Define early stopping criteria
early_stop_patience = 3
early_stop_counter = 0
best_val_accuracy = 0


# Configure logging
logger = logging.getLogger(__name__)
logger.setLevel(logging.INFO)
file_handler = logging.FileHandler('training.log')
stream_handler = logging.StreamHandler()
formatter = logging.Formatter('%(asctime)s [%(levelname)s] %(message)s')
file_handler.setFormatter(formatter)
stream_handler.setFormatter(formatter)
logger.addHandler(file_handler)
logger.addHandler(stream_handler)


# Perform manual hyperparameter tuning
for lr in param_grid['learning_rate']:
    for epochs in param_grid['num_train_epochs']:
        for batch_size in param_grid['train_batch_size']:
            logger.info(f"Training with lr={lr}, epochs={epochs}, batch_size={batch_size}")

            # Initialize the model with current hyperparameters
            args = NERArgs()
            args.learning_rate = lr
            args.num_train_epochs = epochs
            args.train_batch_size = batch_size
            model = NERModel('bert', 'dmis-lab/biobert-base-cased-v1.2', args=args, labels=bio_label, use_cuda=False)


            # Train the model
            for epoch in range(epochs):
                model.train_model(train_data)

                # Evaluate on validation set
                _, _, val_preds = model.eval_model(val_data)
                val_accuracy = accuracy_score(val_data['labels'], val_preds)

                # Check for early stopping
                if val_accuracy > best_val_accuracy:
                    best_val_accuracy = val_accuracy
                    early_stop_counter = 0
                else:
                    early_stop_counter += 1
                    if early_stop_counter >= early_stop_patience:
                        logger.info(f"Early stopping after {epoch + 1} epochs.")
                        break

            # Evaluate on test set
            _, _, test_preds = model.eval_model(test_data)
            accuracy = accuracy_score(test_data['labels'], test_preds)
            logger.info(f"Accuracy: {accuracy:.4f}")

            # Update best parameters and accuracy
            if accuracy > best_accuracy:
                best_accuracy = accuracy
                best_params = {'learning_rate': lr, 'num_train_epochs': epochs, 'train_batch_size': batch_size}

# Log best hyperparameters and accuracy
logger.info("Best Parameters: %s", str(best_params))
logger.info("Best Accuracy: %.4f", best_accuracy)


Some weights of BertForTokenClassification were not initialized from the model checkpoint at dmis-lab/biobert-base-cased-v1.2 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
2024-03-23 10:55:18,864 [INFO] Training with lr=1e-05, epochs=1, batch_size=16
2024-03-23 10:55:18,864 [INFO] Training with lr=1e-05, epochs=1, batch_size=16
2024-03-23 10:55:18,864 [INFO] Training with lr=1e-05, epochs=1, batch_size=16
2024-03-23 10:55:18,864 [INFO] Training with lr=1e-05, epochs=1, batch_size=16
2024-03-23 10:55:18,864 [INFO] Training with lr=1e-05, epochs=1, batch_size=16
Some weights of BertForTokenClassification were not initialized from the model checkpoint at dmis-lab/biobert-base-cased-v1.2 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and infere

KeyboardInterrupt: 

Regularization

In [62]:

# Define regularization parameters
args = NERArgs()
args.num_train_epochs = 5
args.learning_rate = 2e-5
args.overwrite_output_dir = True
args.train_batch_size = 32
args.eval_batch_size = 32
args.weight_decay = 0.01  # Example regularization parameter

# Initialize the model with regularization
model = NERModel('bert', 'dmis-lab/biobert-base-cased-v1.2', args=args, labels=bio_label, use_cuda=False)

# Train the model
model.train_model(train_data)

# Evaluate the model
result, model_outputs, preds_list = model.eval_model(test_data)
print(result)


Some weights of BertForTokenClassification were not initialized from the model checkpoint at dmis-lab/biobert-base-cased-v1.2 and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Running Evaluation: 100%|██████████| 16/16 [01:56<00:00,  7.31s/it]


{'eval_loss': 0.05003013802343048, 'precision': 0.0, 'recall': 0.0, 'f1_score': 0.0}


C:\Users\okechukwu chude\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\seqeval\metrics\v1.py:57: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


In [63]:
result

{'eval_loss': 0.05003013802343048,
 'precision': 0.0,
 'recall': 0.0,
 'f1_score': 0.0}

Fine-tuning BERT for named-entity recognition

In [76]:

label2id = {k: v for v, k in enumerate(token_df.label.unique())}
id2label = {v: k for v, k in enumerate(token_df.label.unique())}
label2id

{'O': 0, 'B': 1, 'I': 2}

#### **Preparing the dataset and dataloader**

In [100]:
from transformers import BertTokenizer, BertForMaskedLM

In [101]:
MAX_LEN = 128
TRAIN_BATCH_SIZE = 4
VALID_BATCH_SIZE = 2
EPOCHS = 1
LEARNING_RATE = 1e-05
MAX_GRAD_NORM = 10
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')


tokenizer_config.json: 100%|██████████| 48.0/48.0 [00:00<00:00, 47.7kB/s]
C:\Users\okechukwu chude\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\huggingface_hub\file_download.py:149: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\okechukwu chude\.cache\huggingface\hub\models--bert-base-uncased. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to see activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-s

In [120]:
import torch
from torch.utils.data import Dataset

class dataset(Dataset):
    def __init__(self, dataframe, tokenizer, max_len):
        self.len = len(dataframe)
        self.data = dataframe
        self.tokenizer = tokenizer
        self.max_len = max_len

    def __getitem__(self, index):
        words = self.data.iloc[index]['word'].split(",")  # Assuming tokenized words are separated by comma
        labels = self.data.iloc[index]['label'].split(",")

        # Convert tokenized words to token IDs
        ids = [self.tokenizer.convert_tokens_to_ids(word.split()) for word in words]

        # Pad or truncate tokenized words and labels to fit MAX_LEN
        if len(ids) > self.max_len:
            ids = ids[:self.max_len]
            labels = labels[:self.max_len]
        elif len(ids) < self.max_len:
            padding_length = self.max_len - len(ids)
            ids += [[0]] * padding_length  # Padding token ID assumed to be 0
            labels += ['O'] * padding_length

        # Flatten the list of token IDs
        ids = [token_id for sublist in ids for token_id in sublist]

        # Convert labels to label ids
        label_ids = [label2id[label] for label in labels]

        # Create attention mask
        attn_mask = [1 if token_id != 0 else 0 for token_id in ids]  # Assuming padding token ID is 0

        return {
            'ids': torch.tensor(ids, dtype=torch.long),
            'mask': torch.tensor(attn_mask, dtype=torch.long),
            'targets': torch.tensor(label_ids, dtype=torch.long)
        }

    def __len__(self):
        return self.len



In [121]:
# Define train and test datasets using train_test_split
train_df, test_df = train_test_split(token_df, test_size=0.2, random_state=42)

print("FULL Dataset: {}".format(token_df.shape))
print("TRAIN Dataset: {}".format(train_df.shape))
print("TEST Dataset: {}".format(test_df.shape))

# Create dataset instances
training_set = dataset(train_df, tokenizer, MAX_LEN)
testing_set = dataset(test_df, tokenizer, MAX_LEN)

FULL Dataset: (472267, 3)
TRAIN Dataset: (377813, 3)
TEST Dataset: (94454, 3)


In [122]:
training_set[0]

{'ids': tensor([100,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
           0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
           0,   0]),
 'mask': tensor([1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0

In [123]:
training_set[0]["ids"]

tensor([100,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,   0,
          0,   0])

In [125]:
# print the first 30 tokens and corresponding labels
for token, label in zip(tokenizer.convert_ids_to_tokens(training_set[0]["ids"][:30]), training_set[0]["targets"][:30]):
  print('{0:10}  {1}'.format(token, id2label[label.item()]))

[UNK]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O
[PAD]       O


Now, let's define the corresponding PyTorch dataloaders:

In [126]:
train_params = {'batch_size': TRAIN_BATCH_SIZE,
                'shuffle': True,
                'num_workers': 0
                }

test_params = {'batch_size': VALID_BATCH_SIZE,
                'shuffle': True,
                'num_workers': 0
                }

training_loader = DataLoader(training_set, **train_params)
testing_loader = DataLoader(testing_set, **test_params)

#### **Defining the model**

In [128]:
from transformers import BertTokenizer, BertConfig, BertForTokenClassification


from torch import cuda
device = 'cuda' if cuda.is_available() else 'cpu'
print(device)

cpu


In [129]:
model = BertForTokenClassification.from_pretrained('bert-base-uncased', 
                                                   num_labels=len(id2label),
                                                   id2label=id2label,
                                                   label2id=label2id)
model.to(device)

model.safetensors: 100%|██████████| 440M/440M [07:21<00:00, 997kB/s]  
Some weights of BertForTokenClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


BertForTokenClassification(
  (bert): BertModel(
    (embeddings): BertEmbeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (token_type_embeddings): Embedding(2, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0-11): 12 x BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-12, el